In [1]:
module BTP
  class AdjacencyMatrix2
    def initialize(path)
      @path      = path
      @words     = []
      @alphabets = []
    end

    def parse(summa_data=nil)
      @words = if summa_data
                 summa_data
               else
                 File
                   .read(@path)
                   .split("\n")
                   .map { |line| line.split("\t") }
                   .keep_if { |line| line[0].include?('pos=N') }
                   .map { |line| line[1] }
               end

      compute_counters(@words)

      @alphabets = @words.map { |word| word.split('') }.flatten.uniq.sort

      puts "Unique alphabets: #{@alphabets}"
      puts "Unique alphabets count: #{@alphabets.count}"

      @fields = @alphabets.map do |alphabet|
        [
          alphabet,
          (0..@left_most).map { |i| "#{alphabet}_#{i}" },
          (@right_most..-1).map { |j| "#{alphabet}_#{j}" },
          (0..@left_most).map do |i|
            (@right_most..-1).map do |j|
              "#{alphabet}_#{i}_#{j}"
            end
          end
        ]
      end.flatten

      puts "DataFrame size: #{@fields.count} = "\
           "#{@alphabets.count}*#{@left_most+1}*#{@left_most+1} + "\
           "#{@alphabets.count}*#{@left_most+1}*2 + #{@alphabets.count}"

      @dataframe = Daru::DataFrame.new({}, order: @fields, index: @fields)
      @words.each { |word| adjacency_matrix(word) }
      @dataframe.replace_values(nil, 0)

      @dataframe
    end

    private

    def compute_counters(words)
      total = 0.0
      length_frequency = Hash
                         .new(0)
                         .tap { |h| words.map(&:size).each { |word| h[word] += 1 } }
                         .sort_by { |k, _v| k }
                         .map { |k, v| [k, (total+=v)] }
                         .map { |k, v| [k, v/total] }
                         .to_h

      @left_most  = (length_frequency.find { |_k, v| v > 0.7 }.first - 1).freeze
      @right_most = (-1 * @left_most - 1).freeze

      puts "Left most: #{@left_most+1}"
    end

    def adjacency_matrix(word)
      i = 0
      word_length = word.length

      while i < word_length
        j = i+1
        while j < word_length
          update_adjacency_matrix(i, i - word_length, word[i], j, j - word_length, word[j])
          update_adjacency_matrix(j, j - word_length, word[j], i, i - word_length, word[i])
          j += 1
        end
        i += 1
      end
    end

    def update_adjacency_matrix(left1, right1, char1, left2, right2, char2)
      update_at("#{char1}_#{left1}_#{right1}", "#{char2}_#{left2}_#{right2}") if left1 < @left_most && left2 < @left_most && right1 > @right_most && right2 > @right_most
      update_at("#{char1}_#{right1}", "#{char2}_#{left2}_#{right2}") if left2 < @left_most && right1 > @right_most && right2 > @right_most
      update_at("#{char1}_#{left1}", "#{char2}_#{left2}_#{right2}") if left1 < @left_most && left2 < @left_most && right2 > @right_most
      update_at(char1, "#{char2}_#{left2}_#{right2}") if left2 < @left_most && right2 > @right_most

      update_at("#{char1}_#{left1}_#{right1}", "#{char2}_#{right2}") if left1 < @left_most && right1 > @right_most && right2 > @right_most
      update_at("#{char1}_#{right1}", "#{char2}_#{right2}") if right1 > @right_most && right2 > @right_most
      update_at("#{char1}_#{left1}", "#{char2}_#{right2}") if left1 < @left_most && right2 > @right_most
      update_at(char1, "#{char2}_#{right2}") if right2 > @right_most

      update_at("#{char1}_#{left1}_#{right1}", "#{char2}_#{left2}") if left1 < @left_most && left2 < @left_most && right1 > @right_most
      update_at("#{char1}_#{right1}", "#{char2}_#{left2}") if left2 < @left_most && right1 > @right_most
      update_at("#{char1}_#{left1}", "#{char2}_#{left2}") if left1 < @left_most && left2 < @left_most
      update_at(char1, "#{char2}_#{left2}") if left2 < @left_most

      update_at("#{char1}_#{left1}_#{right1}", char2) if left1 < @left_most && right1 > @right_most
      update_at("#{char1}_#{right1}", char2) if right1 > @right_most
      update_at("#{char1}_#{left1}", char2) if left1 < @left_most
      update_at(char1, char2)
    end

    def update_at(key1, key2)
      if @dataframe[key1][key2]
        @dataframe[key1][key2] += 1
      else
        @dataframe[key1][key2] = 1
      end
    end
  end
end


:update_at

In [2]:
require 'daru'


Install the spreadsheet gem version ~>1.1.1 for using spreadsheet functions.

Install the mechanize gem version ~>2.7.5 for using mechanize functions.


true

In [3]:
df = BTP::AdjacencyMatrix2.new('../../spec/fixtures/maltese/maltese-task2-train').parse

Left most: 8
Unique alphabets: ["a", "b", "d", "e", "f", "g", "h", "i", "j", "k", "l", "m", "n", "o", "p", "q", "r", "s", "t", "u", "v", "w", "x", "z", "à", "ċ", "ġ", "ħ", "ż"]
Unique alphabets count: 29
DataFrame size: 2349 = 29*8*8 + 29*8*2 + 29


#<Daru::DataFrame(2349x2349)>
             a    a_0    a_1    a_2    a_3    a_4    a_5    a_6    a_7   a_-8   a_-7   a_-6   a_-5   a_-4   a_-3   a_-2   a_-1 a_0_-8 a_0_-7 a_0_-6 a_0_-5 a_0_-4 a_0_-3 a_0_-2 a_0_-1 a_1_-8 a_1_-7 a_1_-6 a_1_-5 a_1_-4 a_1_-3 a_1_-2 a_1_-1 a_2_-8 a_2_-7 a_2_-6 a_2_-5 a_2_-4 a_2_-3 a_2_-2 a_2_-1 a_3_-8 a_3_-7 a_3_-6 a_3_-5 a_3_-4 a_3_-3 a_3_-2 a_3_-1 a_4_-8 a_4_-7 a_4_-6 a_4_-5 a_4_-4 a_4_-3 a_4_-2 a_4_-1 a_5_-8 a_5_-7 a_5_-6 a_5_-5 a_5_-4 a_5_-3 a_5_-2 a_5_-1 a_6_-8 a_6_-7 a_6_-6 a_6_-5 a_6_-4 a_6_-3 a_6_-2 a_6_-1 a_7_-8 a_7_-7 a_7_-6 a_7_-5 a_7_-4 a_7_-3 a_7_-2 a_7_-1      b    b_0    b_1    b_2    b_3    b_4    b_5    b_6    b_7   b_-8   b_-7   b_-6   b_-5   b_-4   b_-3   b_-2   b_-1 b_0_-8 b_0_-7 b_0_-6 b_0_-5 b_0_-4 b_0_-3 b_0_-2 b_0_-1 b_1_-8 b_1_-7 b_1_-6 b_1_-5 b_1_-4 b_1_-3 b_1_-2 b_1_-1 b_2_-8 b_2_-7 b_2_-6 b_2_-5 b_2_-4 b_2_-3 b_2_-2 b_2_-1 b_3_-8 b_3_-7 b_3_-6 b_3_-5 b_3_-4 b_3_-3 b_3_-2 b_3_-1 b_4_-8 b_4_-7 b_4_-6 b_4_-5 b_4_-4 b_4_-3 b_4_-2 b_4_-1 b_5_-8 b_5_-7 b_5_-6 b_5_-5 b_5_-4 b_5_-3 b_5_-2 b_5_-1 b_6_-8 b_6_-7 b_6_-6 b_6_-5 b_6_-4 b_6_-3 b_6_-2 b_6_-1 b_7_-8 b_7_-7 b_7_-6 b_7_-5 b_7_-4 b_7_-3 b_7_-2 b_7_-1      d    d_0    d_1    d_2    d_3    d_4    d_5    d_6    d_7   d_-8   d_-7   d_-6   d_-5   d_-4   d_-3   d_-2   d_-1 d_0_-8 d_0_-7 d_0_-6 d_0_-5 d_0_-4 d_0_-3 d_0_-2 d_0_-1 d_1_-8 d_1_-7 d_1_-6 d_1_-5 d_1_-4 d_1_-3 d_1_-2 d_1_-1 d_2_-8 d_2_-7 d_2_-6 d_2_-5 d_2_-4 d_2_-3 d_2_-2 d_2_-1 d_3_-8 d_3_-7 d_3_-6 d_3_-5 d_3_-4 d_3_-3 d_3_-2 d_3_-1 d_4_-8 d_4_-7 d_4_-6 d_4_-5 d_4_-4 d_4_-3 d_4_-2 d_4_-1 d_5_-8 d_5_-7 d_5_-6 d_5_-5 d_5_-4 d_5_-3 d_5_-2 d_5_-1 d_6_-8 d_6_-7 d_6_-6 d_6_-5 d_6_-4 d_6_-3 d_6_-2 d_6_-1 d_7_-8 d_7_-7 d_7_-6 d_7_-5 d_7_-4 d_7_-3 d_7_-2 d_7_-1      e    e_0    e_1    e_2    e_3    e_4    e_5    e_6    e_7   e_-8   e_-7   e_-6   e_-5   e_-4   e_-3   e_-2   e_-1 e_0_-8 e_0_-7 e_0_-6 e_0_-5 e_0_-4 e_0_-3 e_0_-2 e_0_-1 e_1_-8 e_1_-7 e_1_-6 e_1_-5 e_1_-4 e_1_-3 e_1_-2 e_1_-1 e_2_-8 e_2_-7 e_2_-6 e_2_-5 e_2_-4 e_2_-3 e_2_-2 e_2_-1 e_3_-8 e_3_-7 e_3_-6 e_3_-5 e_3_-4 e_3_-3 e_3_-2 e_3_-1 e_4_-8 e_4_-7 e_4_-6 e_4_-5 e_4_-4 e_4_-3 e_4_-2 e_4_-1 e_5_-8 e_5_-7 e_5_-6 e_5_-5 e_5_-4 e_5_-3 e_5_-2 e_5_-1 e_6_-8 e_6_-7 e_6_-6 e_6_-5 e_6_-4 e_6_-3 e_6_-2 e_6_-1 e_7_-8 e_7_-7 e_7_-6 e_7_-5 e_7_-4 e_7_-3 e_7_-2 e_7_-1      f    f_0    f_1    f_2    f_3    f_4    f_5    f_6    f_7   f_-8   f_-7   f_-6   f_-5   f_-4   f_-3   f_-2   f_-1 f_0_-8 f_0_-7 f_0_-6 f_0_-5 f_0_-4 f_0_-3 f_0_-2 f_0_-1 f_1_-8 f_1_-7 f_1_-6 f_1_-5 f_1_-4 f_1_-3 f_1_-2 f_1_-1 f_2_-8 f_2_-7 f_2_-6 f_2_-5 f_2_-4 f_2_-3 f_2_-2 f_2_-1 f_3_-8 f_3_-7 f_3_-6 f_3_-5 f_3_-4 f_3_-3 f_3_-2 f_3_-1 f_4_-8 f_4_-7 f_4_-6 f_4_-5 f_4_-4 f_4_-3 f_4_-2 f_4_-1 f_5_-8 f_5_-7 f_5_-6 f_5_-5 f_5_-4 f_5_-3 f_5_-2 f_5_-1 f_6_-8 f_6_-7 f_6_-6 f_6_-5 f_6_-4 f_6_-3 f_6_-2 f_6_-1 f_7_-8 f_7_-7 f_7_-6 f_7_-5 f_7_-4 f_7_-3 f_7_-2 f_7_-1      g    g_0    g_1    g_2    g_3    g_4    g_5    g_6    g_7   g_-8   g_-7   g_-6   g_-5   g_-4   g_-3   g_-2   g_-1 g_0_-8 g_0_-7 g_0_-6 g_0_-5 g_0_-4 g_0_-3 g_0_-2 g_0_-1 g_1_-8 g_1_-7 g_1_-6 g_1_-5 g_1_-4 g_1_-3 g_1_-2 g_1_-1 g_2_-8 g_2_-7 g_2_-6 g_2_-5 g_2_-4 g_2_-3 g_2_-2 g_2_-1 g_3_-8 g_3_-7 g_3_-6 g_3_-5 g_3_-4 g_3_-3 g_3_-2 g_3_-1 g_4_-8 g_4_-7 g_4_-6 g_4_-5 g_4_-4 g_4_-3 g_4_-2 g_4_-1 g_5_-8 g_5_-7 g_5_-6 g_5_-5 g_5_-4 g_5_-3 g_5_-2 g_5_-1 g_6_-8 g_6_-7 g_6_-6 g_6_-5 g_6_-4 g_6_-3 g_6_-2 g_6_-1 g_7_-8 g_7_-7 g_7_-6 g_7_-5 g_7_-4 g_7_-3 g_7_-2 g_7_-1      h    h_0    h_1    h_2    h_3    h_4    h_5    h_6    h_7   h_-8   h_-7   h_-6   h_-5   h_-4   h_-3   h_-2   h_-1 h_0_-8 h_0_-7 h_0_-6 h_0_-5 h_0_-4 h_0_-3 h_0_-2 h_0_-1 h_1_-8 h_1_-7 h_1_-6 h_1_-5 h_1_-4 h_1_-3 h_1_-2 h_1_-1 h_2_-8 h_2_-7 h_2_-6 h_2_-5 h_2_-4 h_2_-3 h_2_-2 h_2_-1 h_3_-8 h_3_-7 h_3_-6 h_3_-5 h_3_-4 h_3_-3 h_3_-2 h_3_-1 h_4_-8 h_4_-7 h_4_-6 h_4_-5 h_4_-4 h_4_-3 h_4_-2 h_4_-1 h_5_-8 h_5_-7 h_5_-6 h_5_-5 h_5_-4 h_5_-3 h_5_-2 h_5_-1 h_6_-8 h_6_-7 h_6_-6 h_6_-5 h_6_-4 h_6_-3 h_6_-2 h_6_-1 h_7_-8 h_7_-7 h_7_-6 h_7_-5 h_7_-4 h_7_-3 h_7_-2 

In [4]:
df.max.sort(ascending: false)

#<Daru::Vector(2349)>
       max
    i  187
    t  187
    a  161
    e  125
    r  112
    n   97
  t_0   80
 i_-3   75
 a_-1   68
    j   67
    s   63
    o   62
    m   61
  i_4   56
    z   54
  ...  ...

In [5]:
df.write_csv 'x.csv'

In [6]:
df['t']['t']

104

In [12]:
module BTP
  class AdjacencyMatrixHindi
    def initialize(path)
      @path      = path
      @words     = []
      @alphabets = []
    end

    def parse(summa_data=nil)
      @words = if summa_data
                 summa_data.uniq
               else
                 File
                   .read(@path)
                   .split("\n")
                   .map { |line| line.split("\t") }
                   .map(&:first)
                   .uniq
               end

      compute_counters(@words)

      @alphabets = @words.map { |word| word.split('') }.flatten.uniq.sort

      puts "Unique alphabets: #{@alphabets}"
      puts "Unique alphabets count: #{@alphabets.count}"
      puts "Words count: #{@words.count}"
    
      @fields = @alphabets.map do |alphabet|
        [
          alphabet,
          (0..@left_most-1).map { |i| "#{alphabet}_#{i}" },
          (@right_most+1..-1).map { |j| "#{alphabet}_#{j}" },
          (0..@left_most-1).map do |i|
            (@right_most+1..-1).map do |j|
              "#{alphabet}_#{i}_#{j}"
            end
          end
        ]
      end.flatten

      puts "DataFrame size: #{@fields.count} = "\
           "#{@alphabets.count}*#{@left_most}*#{@left_most} + "\
           "#{@alphabets.count}*#{@left_most}*2 + #{@alphabets.count}"

      @dataframe = Daru::DataFrame.new({}, order: @fields, index: @fields)
      @words.each { |word| adjacency_matrix(word) }
      @dataframe.replace_values(nil, 0)

      @dataframe
    end

    private

    def compute_counters(words)
      total = 0.0
      length_frequency = Hash
                         .new(0)
                         .tap { |h| words.map(&:size).each { |word| h[word] += 1 } }
                         .sort_by { |k, _v| k }
                         .map { |k, v| [k, (total+=v)] }
                         .map { |k, v| [k, v/total] }
                         .to_h

      @left_most  = (length_frequency.find { |_k, v| v > 0.7 }.first - 1).freeze
      @right_most = (-1 * @left_most - 1).freeze

      puts "Left most: #{@left_most}"
    end

    def adjacency_matrix(word)
      i = 0
      word_length = word.length

      while i < word_length
        j = i+1
        while j < word_length
          update_adjacency_matrix(i, i - word_length, word[i], j, j - word_length, word[j])
          update_adjacency_matrix(j, j - word_length, word[j], i, i - word_length, word[i])
          j += 1
        end
        i += 1
      end
    end

    def update_adjacency_matrix(left1, right1, char1, left2, right2, char2)
      update_at("#{char1}_#{left1}_#{right1}", "#{char2}_#{left2}_#{right2}") if left1 < @left_most && left2 < @left_most && right1 > @right_most && right2 > @right_most
      update_at("#{char1}_#{right1}", "#{char2}_#{left2}_#{right2}") if left2 < @left_most && right1 > @right_most && right2 > @right_most
      update_at("#{char1}_#{left1}", "#{char2}_#{left2}_#{right2}") if left1 < @left_most && left2 < @left_most && right2 > @right_most
      update_at(char1, "#{char2}_#{left2}_#{right2}") if left2 < @left_most && right2 > @right_most

      update_at("#{char1}_#{left1}_#{right1}", "#{char2}_#{right2}") if left1 < @left_most && right1 > @right_most && right2 > @right_most
      update_at("#{char1}_#{right1}", "#{char2}_#{right2}") if right1 > @right_most && right2 > @right_most
      update_at("#{char1}_#{left1}", "#{char2}_#{right2}") if left1 < @left_most && right2 > @right_most
      update_at(char1, "#{char2}_#{right2}") if right2 > @right_most

      update_at("#{char1}_#{left1}_#{right1}", "#{char2}_#{left2}") if left1 < @left_most && left2 < @left_most && right1 > @right_most
      update_at("#{char1}_#{right1}", "#{char2}_#{left2}") if left2 < @left_most && right1 > @right_most
      update_at("#{char1}_#{left1}", "#{char2}_#{left2}") if left1 < @left_most && left2 < @left_most
      update_at(char1, "#{char2}_#{left2}") if left2 < @left_most

      update_at("#{char1}_#{left1}_#{right1}", char2) if left1 < @left_most && right1 > @right_most
      update_at("#{char1}_#{right1}", char2) if right1 > @right_most
      update_at("#{char1}_#{left1}", char2) if left1 < @left_most
      update_at(char1, char2)
    end


    def update_at(key1, key2)
      if @dataframe[key1][key2]
        @dataframe[key1][key2] += 1
      else
        @dataframe[key1][key2] = 1
      end
    end
  end
end
hindi_df = BTP::AdjacencyMatrixHindi.new('../../spec/fixtures/hindi/hindi-train-low').parse


Left most: 6
Unique alphabets: [" ", "ँ", "ं", "अ", "इ", "उ", "ऐ", "क", "ख", "ग", "घ", "च", "छ", "ज", "झ", "ट", "ठ", "ड", "ढ", "त", "थ", "द", "ध", "न", "प", "फ", "ब", "म", "य", "र", "ल", "व", "श", "स", "ह", "़", "ा", "ि", "ी", "ु", "ू", "े", "ै", "ो", "्"]
Unique alphabets count: 45
Words count: 85
DataFrame size: 2205 = 45*6*6 + 45*6*2 + 45


#<Daru::DataFrame(2205x2205)>
                   _0     _1     _2     _3     _4     _5    _-6    _-5    _-4    _-3    _-2    _-1  _0_-6  _0_-5  _0_-4  _0_-3  _0_-2  _0_-1  _1_-6  _1_-5  _1_-4  _1_-3  _1_-2  _1_-1  _2_-6  _2_-5  _2_-4  _2_-3  _2_-2  _2_-1  _3_-6  _3_-5  _3_-4  _3_-3  _3_-2  _3_-1  _4_-6  _4_-5  _4_-4  _4_-3  _4_-2  _4_-1  _5_-6  _5_-5  _5_-4  _5_-3  _5_-2  _5_-1      ँ    ँ_0    ँ_1    ँ_2    ँ_3    ँ_4    ँ_5   ँ_-6   ँ_-5   ँ_-4   ँ_-3   ँ_-2   ँ_-1 ँ_0_-6 ँ_0_-5 ँ_0_-4 ँ_0_-3 ँ_0_-2 ँ_0_-1 ँ_1_-6 ँ_1_-5 ँ_1_-4 ँ_1_-3 ँ_1_-2 ँ_1_-1 ँ_2_-6 ँ_2_-5 ँ_2_-4 ँ_2_-3 ँ_2_-2 ँ_2_-1 ँ_3_-6 ँ_3_-5 ँ_3_-4 ँ_3_-3 ँ_3_-2 ँ_3_-1 ँ_4_-6 ँ_4_-5 ँ_4_-4 ँ_4_-3 ँ_4_-2 ँ_4_-1 ँ_5_-6 ँ_5_-5 ँ_5_-4 ँ_5_-3 ँ_5_-2 ँ_5_-1      ं    ं_0    ं_1    ं_2    ं_3    ं_4    ं_5   ं_-6   ं_-5   ं_-4   ं_-3   ं_-2   ं_-1 ं_0_-6 ं_0_-5 ं_0_-4 ं_0_-3 ं_0_-2 ं_0_-1 ं_1_-6 ं_1_-5 ं_1_-4 ं_1_-3 ं_1_-2 ं_1_-1 ं_2_-6 ं_2_-5 ं_2_-4 ं_2_-3 ं_2_-2 ं_2_-1 ं_3_-6 ं_3_-5 ं_3_-4 ं_3_-3 ं_3_-2 ं_3_-1 ं_4_-6 ं_4_-5 ं_4_-4 ं_4_-3 ं_4_-2 ं_4_-1 ं_5_-6 ं_5_-5 ं_5_-4 ं_5_-3 ं_5_-2 ं_5_-1      अ    अ_0    अ_1    अ_2    अ_3    अ_4    अ_5   अ_-6   अ_-5   अ_-4   अ_-3   अ_-2   अ_-1 अ_0_-6 अ_0_-5 अ_0_-4 अ_0_-3 अ_0_-2 अ_0_-1 अ_1_-6 अ_1_-5 अ_1_-4 अ_1_-3 अ_1_-2 अ_1_-1 अ_2_-6 अ_2_-5 अ_2_-4 अ_2_-3 अ_2_-2 अ_2_-1 अ_3_-6 अ_3_-5 अ_3_-4 अ_3_-3 अ_3_-2 अ_3_-1 अ_4_-6 अ_4_-5 अ_4_-4 अ_4_-3 अ_4_-2 अ_4_-1 अ_5_-6 अ_5_-5 अ_5_-4 अ_5_-3 अ_5_-2 अ_5_-1      इ    इ_0    इ_1    इ_2    इ_3    इ_4    इ_5   इ_-6   इ_-5   इ_-4   इ_-3   इ_-2   इ_-1 इ_0_-6 इ_0_-5 इ_0_-4 इ_0_-3 इ_0_-2 इ_0_-1 इ_1_-6 इ_1_-5 इ_1_-4 इ_1_-3 इ_1_-2 इ_1_-1 इ_2_-6 इ_2_-5 इ_2_-4 इ_2_-3 इ_2_-2 इ_2_-1 इ_3_-6 इ_3_-5 इ_3_-4 इ_3_-3 इ_3_-2 इ_3_-1 इ_4_-6 इ_4_-5 इ_4_-4 इ_4_-3 इ_4_-2 इ_4_-1 इ_5_-6 इ_5_-5 इ_5_-4 इ_5_-3 इ_5_-2 इ_5_-1      उ    उ_0    उ_1    उ_2    उ_3    उ_4    उ_5   उ_-6   उ_-5   उ_-4   उ_-3   उ_-2   उ_-1 उ_0_-6 उ_0_-5 उ_0_-4 उ_0_-3 उ_0_-2 उ_0_-1 उ_1_-6 उ_1_-5 उ_1_-4 उ_1_-3 उ_1_-2 उ_1_-1 उ_2_-6 उ_2_-5 उ_2_-4 उ_2_-3 उ_2_-2 उ_2_-1 उ_3_-6 उ_3_-5 उ_3_-4 उ_3_-3 उ_3_-2 उ_3_-1 उ_4_-6 उ_4_-5 उ_4_-4 उ_4_-3 उ_4_-2 उ_4_-1 उ_5_-6 उ_5_-5 उ_5_-4 उ_5_-3 उ_5_-2 उ_5_-1      ऐ    ऐ_0    ऐ_1    ऐ_2    ऐ_3    ऐ_4    ऐ_5   ऐ_-6   ऐ_-5   ऐ_-4   ऐ_-3   ऐ_-2   ऐ_-1 ऐ_0_-6 ऐ_0_-5 ऐ_0_-4 ऐ_0_-3 ऐ_0_-2 ऐ_0_-1 ऐ_1_-6 ऐ_1_-5 ऐ_1_-4 ऐ_1_-3 ऐ_1_-2 ऐ_1_-1 ऐ_2_-6 ऐ_2_-5 ऐ_2_-4 ऐ_2_-3 ऐ_2_-2 ऐ_2_-1 ऐ_3_-6 ऐ_3_-5 ऐ_3_-4 ऐ_3_-3 ऐ_3_-2 ऐ_3_-1 ऐ_4_-6 ऐ_4_-5 ऐ_4_-4 ऐ_4_-3 ऐ_4_-2 ऐ_4_-1 ऐ_5_-6 ऐ_5_-5 ऐ_5_-4 ऐ_5_-3 ऐ_5_-2 ऐ_5_-1      क    क_0    क_1    क_2    क_3    क_4    क_5   क_-6   क_-5   क_-4   क_-3   क_-2   क_-1 क_0_-6 क_0_-5 क_0_-4 क_0_-3 क_0_-2 क_0_-1 क_1_-6 क_1_-5 क_1_-4 क_1_-3 क_1_-2 क_1_-1 क_2_-6 क_2_-5 क_2_-4 क_2_-3 क_2_-2 क_2_-1 क_3_-6 क_3_-5 क_3_-4 क_3_-3 क_3_-2 क_3_-1 क_4_-6 क_4_-5 क_4_-4 क_4_-3 क_4_-2 क_4_-1 क_5_-6 क_5_-5 क_5_-4 क_5_-3 क_5_-2 क_5_-1      ख    ख_0    ख_1    ख_2    ख_3    ख_4    ख_5   ख_-6   ख_-5   ख_-4   ख_-3   ख_-2   ख_-1 ख_0_-6 ख_0_-5 ख_0_-4 ख_0_-3 ख_0_-2 ख_0_-1 ख_1_-6 ख_1_-5 ख_1_-4 ख_1_-3 ख_1_-2 ख_1_-1 ख_2_-6 ख_2_-5 ख_2_-4 ख_2_-3 ख_2_-2 ख_2_-1 ख_3_-6 ख_3_-5 ख_3_-4 ख_3_-3 ख_3_-2 ख_3_-1 ख_4_-6 ख_4_-5 ख_4_-4 ख_4_-3 ख_4_-2 ख_4_-1 ख_5_-6 ख_5_-5 ख_5_-4 ख_5_-3 ख_5_-2 ख_5_-1      ग    ग_0    ग_1    ग_2    ग_3    ग_4    ग_5   ग_-6   ग_-5   ग_-4   ग_-3   ग_-2   ग_-1 ग_0_-6 ग_0_-5 ग_0_-4 ग_0_-3 ग_0_-2 ग_0_-1 ग_1_-6 ग_1_-5 ग_1_-4 ग_1_-3 ग_1_-2 ग_1_-1 ग_2_-6 ग_2_-5 ग_2_-4 ग_2_-3 ग_2_-2 ग_2_-1 ग_3_-6 ग_3_-5 ग_3_-4 ग_3_-3 ग_3_-2 ग_3_-1 ग_4_-6 ग_4_-5 ग_4_-4 ग_4_-3 ग_4_-2 ग_4_-1 ग_5_-6 ग_5_-5 ग_5_-4 ग_5_-3 ग_5_-2 ग_5_-1      घ    घ_0    घ_1    घ_2    घ_3    घ_4    घ_5   घ_-6   घ_-5   घ_-4   घ_-3   घ_-2   घ_-1 घ_0_-6 घ_0_-5 घ_0_-4 घ_0_-3 घ_0_-2 घ_0_-1 घ_1_-6 घ_1_-5 घ_1_-4 घ_1_-3 घ_1_-2 घ_1_-1 घ_2_-6 घ_2_-5 घ_2_-4 घ_2_-3 घ_2_-2 घ_2_-1 घ_3_-6 घ_3_-5 घ_3_-4 घ_3_-3 घ_3_-2 घ_3_-1 घ_4_-6 घ_4_-5 घ_4_-4 घ_4_-3 घ_4_-2 घ_4_-1 घ_5_-6 घ_5_-5 घ_5_-4 घ_5_-3 घ_5_-2 घ_5_-1      च    च_0    च_1    च_2    च_3    च_4    च_5   च_-6   च_-5   च_-4   च_-3   च_-2   च_-1 च_0_-6 च_0_-5 च_0_-4 च_0_-3 च_0_-2 च_0_-1 च_1_-6 च_1_-5 च_1_-4 च_1_-3 च_1_-2 च_1_-1 च_2_-6 च_2_-5 

In [13]:
# tot = hindi_df.max.sum
# ind = hindi_df.max.index.to_a
# puts tot
# dv = Daru::Vector.new(hindi_df.max.map.with_index { |m, i| [ind[i], m/tot.to_f] }.to_h).sort(ascending: false)
# dv
hindi_df.max.sort(ascending: false)
# hindi_df['न_-5'].max

#<Daru::Vector(2205)>
           max
      ा    157
      न    157
   न_-2    124
   ा_-1    103
      र     66
      क     51
    न_3     43
 न_3_-2     41
            41
   र_-3     40
    ा_4     36
 ा_4_-1     34
    _-5     34
   क_-4     33
      ब     28
    ...    ...

In [9]:
hindi_df.max.max

NoMethodError: undefined method `max' for nil:NilClass